In [25]:
import numpy as np
import pandas as pd
import torch
import json
import matplotlib.pyplot as plt
import sklearn
from sklearn.preprocessing import StandardScaler, MinMaxScaler, Normalizer
from sklearn.cluster import KMeans
from sklearn.model_selection import KFold
import scipy

import torch.nn.functional as F
from torch.utils.data import TensorDataset, DataLoader

from torch import nn
import torch.nn.functional as F
from torch.utils.tensorboard import SummaryWriter

from sklearn.cluster import KMeans

import seaborn as sns

from torcheval.metrics.functional import r2_score

# The main idea is to generate pseudo-labels (aka guessed labels) to computate both Labeled abd Unlabeled losses

In [26]:
device = (
    "cuda"
    if torch.cuda.is_available()
    else "cpu"
)

# semi supervised like
# But x has shape of 40 (burnup + fuel left) features

## Making training-testing tensor datasets under CV split
## The shape of X is [rows, 40]

In [27]:
with open("core_parts.json", "r") as f:
    core_parts = json.load(f)

In [28]:
cores_l = pd.read_excel("input.xlsx", sheet_name="no_burnup")
cores_u = pd.read_excel("burnup_only.xlsx", index_col=0)

In [29]:
fuel_types = cores_l.loc[0, core_parts["fuel_type"]["ALL_CELLS"]].to_numpy()

In [30]:
cores_l.loc[:, core_parts["left"]["ALL_CELLS"]] = fuel_types - cores_l.loc[:, core_parts["burnup"]["ALL_CELLS"]].to_numpy()
cores_u.loc[:, core_parts["left"]["ALL_CELLS"]] = fuel_types - cores_u.loc[:, core_parts["burnup"]["ALL_CELLS"]].to_numpy()

In [31]:
cores_u.loc[:, core_parts["coef"]["ALL_CELLS"]] = None

### Shuffle dataframes before tensorizing

In [32]:
cores_l = cores_l.sample(frac=1)
cores_u = cores_u.sample(frac=1)

In [33]:
cores_l_Xtofit = cores_u.loc[:, 
    [
        *core_parts["burnup"]["ALL_CELLS"],
        *core_parts["left"]["ALL_CELLS"]
    ]
]
cores_l_ytofit = cores_l.loc[:, 
    [
        *core_parts["coef"]["ALL_CELLS"]
    ]
]

In [34]:
mmsX = MinMaxScaler(feature_range=(0,1))
mmsX.fit(cores_l_Xtofit)

mmsy = MinMaxScaler(feature_range=(0,1))
mmsy.fit(cores_l_ytofit)

MinMaxScaler()

In [35]:
# cores_u = cores_l.iloc[80:160, :]
cores_l = cores_l.iloc[:64, :]
# cores_u.loc[:, core_parts["coef"]["ALL_CELLS"]] = None

In [36]:
cores_u.shape, cores_l.shape

((12000, 60), (64, 82))

### Dataset formation

In [37]:
Xl = cores_l.loc[:, 
    [
        *core_parts["burnup"]["ALL_CELLS"],
        *core_parts["left"]["ALL_CELLS"]
    ]
]
yl = cores_l.loc[:, core_parts["coef"]["ALL_CELLS"]]

In [38]:
Xu = cores_u.loc[:, 
    [
        *core_parts["burnup"]["ALL_CELLS"],
        *core_parts["left"]["ALL_CELLS"]
    ]
]
yu = cores_u.loc[:, core_parts["coef"]["ALL_CELLS"]]

In [39]:
Xl = mmsX.transform(Xl)
Xu = mmsX.transform(Xu)

yl = mmsy.transform(yl)


### CV split

In [40]:
ns = 2
kf = KFold(n_splits=ns)
train_size = int(len(Xl) * (ns-1) / ns)
test_size = len(Xl) - train_size
splits_ind = list(kf.split(Xl))
train_size, test_size

(32, 32)

### Started with making batches of tensors

In [41]:

# batch size of labeled data
lbatch = 4
# test set tensor
tbatch = 4

# unlabeled batch size and U to L ratio
cores_l_taken = train_size
cr = 200 * cores_l_taken
print(cr)
RUL = f"{cr}_{cores_l_taken}"

Xu_cr = Xu[:cr]
yu_cr = yu[:cr]

cv_datasets = []
for (train, test) in splits_ind[:ns]:
    Xyl_train = np.concatenate(
        ( Xl[train], yl[train] ),
        axis=1
    )
    Xylb_train = np.asarray(np.split(Xyl_train, len(Xyl_train)/lbatch))
    Xylb_train = np.asarray(Xylb_train).astype("float32")

    # tensor
    Xylb_train_tensor = torch.from_numpy(Xylb_train)

    Xyu_train = np.concatenate(
        (Xu_cr, yu_cr),
        axis=1
    )
    
    Xyub_train = np.asarray(np.split(Xyu_train, len(Xyl_train)/lbatch))
    Xyub_train = np.asarray(Xyub_train).astype("float32")
    
    Xyub_train_tensor = torch.from_numpy(Xyub_train)
    
    Xyl_test = np.concatenate(
        ( Xl[test], yl[test] ),
        axis=1
    )
    
    Xylb_test = np.asarray(np.split(Xyl_test, len(Xyl_test)/tbatch))
    Xylb_test = np.asarray(Xylb_test).astype("float32")
    # tensor
    Xylb_test_tensor = torch.from_numpy(Xylb_test)
    print(
        "train_set: ", Xylb_train_tensor.shape, 
        "test_set: ", Xylb_test_tensor.shape,
        "unlabeled_set: ", Xyub_train_tensor.shape
    )

    # do concat of L and U tensors
    Xy_train_tensor_cat = torch.cat(
        (Xylb_train_tensor, Xyub_train_tensor),
        dim=1
    )
    # shuffle batches
    Xy_train_tensor_cat = Xy_train_tensor_cat[
        torch.randperm(
            Xy_train_tensor_cat.shape[0] #index of batches
        )
    ]
    print(Xy_train_tensor_cat.shape, Xylb_test_tensor.shape)
    # train test tensors split
    inputs = 40
    X_train_tensor = Xy_train_tensor_cat[:, :, :inputs]
    X_test_tensor = Xylb_test_tensor[: , :, :inputs]

    print("Xtrain: ", X_train_tensor.shape)
    print("Xtest: ", X_test_tensor.shape)
    
    y_train_tensor = Xy_train_tensor_cat[:, :, inputs:]
    y_test_tensor = Xylb_test_tensor[: , :, inputs:]

    # tensor dataset
    xy_train = TensorDataset(
        X_train_tensor,
        y_train_tensor
    )
    
    xy_test =  TensorDataset(
        X_test_tensor,
        y_test_tensor,
    )
    # to unpack and iterate over
    cv_datasets.append(
        (xy_train, xy_test)
    )
    

6400
train_set:  torch.Size([8, 4, 60]) test_set:  torch.Size([8, 4, 60]) unlabeled_set:  torch.Size([8, 800, 60])
torch.Size([8, 804, 60]) torch.Size([8, 4, 60])
Xtrain:  torch.Size([8, 804, 40])
Xtest:  torch.Size([8, 4, 40])
train_set:  torch.Size([8, 4, 60]) test_set:  torch.Size([8, 4, 60]) unlabeled_set:  torch.Size([8, 800, 60])
torch.Size([8, 804, 60]) torch.Size([8, 4, 60])
Xtrain:  torch.Size([8, 804, 40])
Xtest:  torch.Size([8, 4, 40])


In [42]:
class SModel(nn.Module):
    def __init__(
        self
    ):
        super().__init__()
        
        # FNN
        self.encodery = nn.Sequential(
            nn.Linear(60, 40),
            nn.ReLU(),
            nn.Linear(40, 20)
        )
        
        self.predictory = nn.Sequential(
            nn.Linear(40, 64),
            nn.ReLU(),
            nn.Linear(64, 20),
            nn.Sigmoid()
        )
        
        self.predictorx = nn.Sequential(
            nn.Linear(20, 64),
            nn.ReLU(),
            nn.Linear(64, 40),
            nn.Sigmoid()
        )
        
        self.decodery = nn.Sequential(
            nn.Linear(50, 64),
            nn.ReLU(),
            nn.Linear(64, 20),
            nn.Sigmoid()
        )
        self.muz = nn.Linear(20, 10)
        self.logvarz = nn.Linear(20, 10)


    
    def forward(
        self,
        x,
    ):
        yhat = self.predictory(x)
        # to get loss of y ---> p(y|x)
        xhat = self.predictorx(yhat)
        
        # encoder takes both x and y -> shape of x+y
        xy = torch.cat(
            (x,yhat), # x is original one
            # (xhat,yhat), # x is hat one
            dim=1
        )
        xy_encoded = self.encodery(xy)
        
        # latent space takes both x and z
        muz, logvarz, z = self.reparametrize(xy_encoded, self.muz, self.logvarz)
        
        # decoder takes both z and y -> shape of y+z
        zy = torch.cat(
            (z, x), # x is original one
            # (z, xhat), # x is hat one
            dim=1
        )
        
        # shape of input x
        y_decoded = self.decodery(zy)
        
        return y_decoded, yhat, xhat, muz, logvarz, z

    def reparametrize(
        self,
        x,
        mu,
        logvar
    ):
        mu = F.relu(
            mu(x)
        )
        logvar = F.relu(
            logvar(x)
        )

        mu = mu.mean(dim=0)
        std = torch.exp(logvar/2).mean(dim=0)
        std_tril = torch.diag_embed(std)
        MVN = torch.distributions.MultivariateNormal(
            mu,
            scale_tril=std_tril
        )
        
        # std = torch.exp(logvar/2)
        # z = mu + std*torch.rand_like(std)
        
        return mu, logvar, MVN.sample(torch.Size([x.shape[0]]))

def reconstruction_loss(
    target,
    pred,
    batch_size
):
    
    recon_loss = F.l1_loss(pred, target, reduction='sum') / batch_size
    # recon_loss = F.l1_loss(pred, target)
    
    return recon_loss

def supervised_loss(
    target,
    pred,
    mu,
    logvar,
    batch_size
):
    xhat_loss = F.l1_loss(pred, target, reduction='sum') / batch_size
 
    kl_loss = -0.5 * torch.sum(1 + logvar - mu.pow(2) - torch.exp(logvar))
    return xhat_loss + kl_loss, xhat_loss, kl_loss
    

# def unsupervised_loss(
#     target_mean,
#     pred, 
#     batch_size
# ):
    
#     yhat_loss = F.l1_loss(pred, target_mean, reduction='sum') / batch_size
#     # print(pred[0], target_mean[0])
#     # yhat_loss = torch.sqrt(yhat_loss)
#     return yhat_loss 

In [43]:
def test(
    model,
    dataset,
    L,
    epoch_num
):

        loss_x_epoch = 0
        r2_epoch = 0

        loss_recon_epoch = 0
        with torch.no_grad():
            for nbatch, (X,y) in enumerate(dataset):
                # so it is shape of [32, 1]
                # y = y[:, 0:1]
                
                
                y = y.to(device)
                y_deep = torch.clone(y)

                X = X.to(device)
                
                y_decoded, yhat, xhat, muz, logvarz, z = model(X)

                loss_x = F.l1_loss(X, xhat, reduction='sum') / X.shape[0]
                
                loss_recon = F.l1_loss(y, y_decoded, reduction='sum') / X.shape[0]
                
                loss_x_epoch += loss_x.item()
                loss_recon_epoch += loss_recon.item()
                
                r2 = r2_score(y, y_decoded, multioutput="raw_values")
                r2_mean = r2.mean()
                r2_epoch += r2_mean.item()

            print(
                "Test on y ",
                y_decoded[0],
                y[0],
                # "\nTest means on y",
                # y_decoded.mean(dim=0),
                # y.mean(dim=0),
                # y_decoded.mean(),
                # y.mean(),
                
            )
            print(
                "Test on x: ",
                X[0],
                xhat[0]
            )
            
            loss_x_epoch = loss_x_epoch / len(dataset)
            loss_recon_epoch = loss_recon_epoch / len(dataset) 
            r2_epoch = r2_epoch / len(dataset)
            
            print(r2_epoch)

            return loss_x_epoch, loss_recon_epoch, r2_epoch
            



In [44]:
def get_row_noise(batch, coef):
    # columns_shape = batch.shape[-1]
    columns_mean = batch.mean(dim=1)

    noise1 = torch.rand(*batch.shape)*coef
    noise2 = torch.rand(*batch.shape)*coef

    noise = noise1 - noise2
    # print(batch[0], noise[0] + batch[0])
    # print(batch[0].mean(), (noise[0] + batch[0]).mean())
    return noise
    
def train(
    model,
    dataset,
    L,
    u,
    r,
    noise_level,
    optimizer,
    epoch_num,
):
        loss_epoch  = 0

        recon_epoch_loss = 0
        
        supervised_epoch_loss = 0
        kl_epoch_loss = 0
    
        xl_epoch_loss = 0
        yresid_epoch_loss = 0
        yu_epoch_loss = 0


        for nbatch, (X,y) in enumerate(dataset):
            # so it is shape of [32, 1]
            # y = y[:, 0:1]
            
            y = y.to(device)
            # left only cell 7-6
            
            
            y_deep = torch.clone(y)

            Xl = X[:lbatch]
            Xu = X[lbatch:]
            # print(Xl.shape, Xu.shape)
            yl = y[:lbatch]
            yu = y[lbatch:]

            Xaug_up = torch.tensor([])
            Xaug_um = torch.tensor([])
            Xaug_lp = torch.tensor([])
            Xaug_lm = torch.tensor([])

            for _ in range(L):
                # aug l part
                
                noise_l = get_row_noise(Xl, noise_level)
                
                Xaug_lp = torch.cat(
                    (
                        Xaug_lp,
                        Xl + noise_l    
                    ),
                    dim=0
                )
                Xaug_lm = torch.cat(
                    (
                        Xaug_lm,
                        Xl - noise_l    
                    ),
                    dim=0
                )
                # print(nbatch, Xl[0])
                
                # aug u part
                noise_u = get_row_noise(Xu, noise_level)
                
                # add
                Xaug_up = torch.cat(
                    (
                        Xaug_up,
                        Xu + noise_u    
                    ),
                    dim=0
                )
                # print(Xu[0], noise_u[0], Xaug_up[0])
                # sub
                Xaug_um = torch.cat(
                    (
                        Xaug_um,
                        Xu - noise_u    
                    ),
                    dim=0
                )
            
            # Zero the gradients
            optimizer.zero_grad()
            
            Xl = Xl.to(device)
            Xu = Xu.to(device)
            
            Xaug_lp = Xaug_lp.to(device)
            Xaug_lm = Xaug_lm.to(device)
            
            Xaug_up = Xaug_up.to(device)
            Xaug_um = Xaug_um.to(device)
            


            if u != 0:

                y_decoded, yhat, xhat, muz, logvarz, z = model(Xl)
                
                reconl_loss = reconstruction_loss(
                    yl,
                    y_decoded,
                    yl.shape[0]
                )
                recon_epoch_loss += reconl_loss.item()
                
                sl_loss, loss_xl, kll_loss = supervised_loss(
                    Xl,
                    xhat,
                    muz,
                    logvarz,
                    Xl.shape[0]
                )
                supervised_epoch_loss += sl_loss.item()
                xl_epoch_loss += loss_xl.item()
                kl_epoch_loss += kll_loss.item()
                
                yu_decoded, yhat_u, xhat, muz, logvarz, z = model(Xu)

                yaug_um_decoded, yaug_um, *_ = model(Xaug_um)
                yaug_up_decoded, yaug_up, *_ = model(Xaug_up)

                # yaug_upm = (yaug_up + yaug_um) / 2
                yaug_upm = (yaug_up_decoded + yaug_um_decoded) / 2
    
                yaug_upm_chunks = torch.reshape(
                    yaug_upm, 
                    (L, int(yaug_upm.shape[0]/L), yaug_upm.shape[-1])
                )
                yaug_upm = yaug_upm_chunks.mean(dim=0)
                
                reconu_loss = reconstruction_loss(
                    yaug_upm,
                    yu_decoded,
                    yhat_u.shape[0]
                )
                
                recon_epoch_loss += reconu_loss.item()*u
                             
                su_loss, loss_xu, klu_loss = supervised_loss(
                    Xu,
                    xhat,
                    muz,
                    logvarz,
                    Xl.shape[0]
                )
                
                supervised_epoch_loss += su_loss.item()*u
                xl_epoch_loss += loss_xu.item()*u
                kl_epoch_loss += klu_loss.item()*u
                
                # loss = r*( u*reconu_loss + reconl_loss ) - u*su_loss + sl_loss
                loss = r*( u*reconu_loss + reconl_loss ) + u*su_loss + sl_loss

            else:
                y_decoded, yhat, xhat, muz, logvarz, z = model(Xl)
                
                recon_loss = reconstruction_loss(
                    yl,
                    y_decoded,
                    yl.shape[0]
                )
                recon_epoch_loss += recon_loss.item()
                
                s_loss, loss_x, kl_loss = supervised_loss(
                    Xl,
                    xhat,
                    muz,
                    logvarz,
                    Xl.shape[0]
                )
                supervised_epoch_loss += s_loss.item()
                xl_epoch_loss += loss_x.item()
                kl_epoch_loss += kl_loss.item()

                yhat_loss = F.l1_loss(yl, yhat, reduction="sum") /  Xl.shape[0]

                # loss = r*recon_loss + s_loss + yhat_loss
                loss = r*recon_loss + s_loss
                
            
            loss.backward()
            optimizer.step()
            
            loss_epoch += loss.item()
            
    
        loss_epoch = loss_epoch / len(dataset)
        recon_epoch_loss = recon_epoch_loss / len(dataset)
        xl_epoch_loss = xl_epoch_loss / len(dataset)
        supervised_epoch_loss = supervised_epoch_loss / len(dataset)
        kl_epoch_loss = kl_epoch_loss / len(dataset)
    
        print(
            xl_epoch_loss,
            recon_epoch_loss,
            kl_epoch_loss
            
        )

        return loss_epoch, recon_epoch_loss, xl_epoch_loss, kl_epoch_loss


        



In [ ]:
# U = [0, 1]
U = [1]
# Ls = [1,2,3,4,5,6,7,8,9,10]
# Ls = [1, 8, 16]
Ls = [4]
# R = [0.01, 0.1, 1]
R = [0.01]
# R = [1]

noise=0.1

for u in U:
    for L in Ls:
        for r in R:
            
            writer = SummaryWriter(f'semi_svae/2splits_cv_1label_noise_{noise}_L_{train_size}_bs_{lbatch}_RUL_{RUL}/L{L}_u_coef_{u}_recon_coef_{r}')
            # writer = SummaryWriter(f'semi_svae/2splits_cv_1label_noise_{noise}_L_{train_size}_bs_{lbatch}_RUL_{RUL}/L{L}_negu_coef_{u}_recon_coef_{r}')
            
            train_loss_cv, train_xl_loss_cv, train_recon_loss_cv, train_kl_loss_cv = [], [], [], []
            test_loss_cv, test_recon_cv, test_r2_cv = [], [], []
            
            # for (xy_train, xy_test) in cv_datasets:
            # instead of cv we do run same model multiple times to average results
            xy_train, xy_test = cv_datasets[0]
            for _ in range(1):
                model = SModel().to(device)
                adam = torch.optim.Adam(model.parameters())
                epoch = 8000
    
                train_loss_epoches, train_xl_loss_epoches, train_recon_loss_epoches, train_kl_loss_epoches = [], [], [], []
                test_loss_epoches, test_recon_epoches, test_r2_epoches = [], [], []
                for e in range(epoch):
                    train_loss_epoch, train_recon_epoch_loss, train_xl_epoch_loss, train_kl_epoch_loss = train(
                        model,
                        xy_train,
                        L,
                        u,
                        r,
                        noise,
                        adam,
                        e
                    )
                    train_loss_epoches.append(train_loss_epoch)
                    train_xl_loss_epoches.append(train_xl_epoch_loss)
                    
                    train_recon_loss_epoches.append(train_recon_epoch_loss)
                    
                    train_kl_loss_epoches.append(train_kl_epoch_loss)
                     
                    test_loss_epoch, test_recon_epoch, test_r2_epoch = test(
                        model,
                        xy_test,
                        L,
                        e
                    )
                    test_loss_epoches.append(test_loss_epoch)
                    test_r2_epoches.append(test_r2_epoch)
                    test_recon_epoches.append(test_recon_epoch)
                
                train_loss_cv.append(train_loss_epoches.copy())
                train_xl_loss_cv.append(train_xl_loss_epoches.copy())
    
                train_recon_loss_cv.append(train_recon_loss_epoches.copy())
                
                train_kl_loss_cv.append(train_kl_loss_epoches.copy())
                
                test_loss_cv.append(test_loss_epoches.copy())
                test_recon_cv.append(test_recon_epoches.copy())
                test_r2_cv.append(test_r2_epoches.copy())
            
            # averaging results over cv
            train_loss_cv = np.asarray(train_loss_cv).mean(axis=0)
            train_xl_loss_cv = np.asarray(train_xl_loss_cv).mean(axis=0)
    
            train_recon_loss_cv =np.asarray(train_recon_loss_cv).mean(axis=0)
            train_kl_loss_cv = np.asarray(train_kl_loss_cv).mean(axis=0)
            
            test_loss_cv = np.asarray(test_loss_cv).mean(axis=0)
            test_recon_cv = np.asarray(test_recon_cv).mean(axis=0)
            test_r2_cv = np.asarray(test_r2_cv).mean(axis=0)
            
            # adding to writer
            for e in range(len(test_loss_cv)):
                # print(e)
                writer.add_scalar('Train/epoch_loss', train_loss_cv[e], global_step=e)
                writer.add_scalar('Train/xl_Loss', train_xl_loss_cv[e], global_step=e)
                writer.add_scalar('Train/kl_Loss', train_kl_loss_cv[e], global_step=e)
                writer.add_scalar('Train/recon_Loss', train_recon_loss_cv[e], global_step=e)
                            
                
                writer.add_scalar('Test/x_loss', test_loss_cv[e], global_step=e)
                writer.add_scalar('Test/recon_loss', test_recon_cv[e], global_step=e)
                writer.add_scalar('Test/r2_mean', test_r2_cv[e], global_step=e)
            # if u == 0:
            #     break

419.6513817310333 3.0667245145887136 7.339521007612348
Test on y  tensor([0.5474, 0.5140, 0.5156, 0.4492, 0.5359, 0.5543, 0.5594, 0.5559, 0.5762,
        0.5566, 0.5576, 0.5267, 0.5448, 0.5669, 0.5342, 0.5792, 0.5430, 0.5225,
        0.4722, 0.4876], device='cuda:0') tensor([0.7238, 0.6479, 0.5038, 0.7558, 0.8372, 0.7593, 0.5119, 0.5844, 0.6830,
        0.1822, 0.8324, 0.4303, 0.5160, 0.4647, 0.4494, 0.3937, 0.6745, 0.6470,
        0.5234, 0.1972], device='cuda:0')
Test on x:  tensor([0.4031, 0.4317, 0.4914, 0.2441, 0.2488, 0.3411, 0.5746, 0.4799, 0.4397,
        0.6828, 0.2274, 0.4960, 0.4808, 0.5513, 0.5776, 0.5757, 0.3343, 0.2897,
        0.3208, 0.6693, 0.5969, 0.5683, 0.5086, 0.7559, 0.7512, 0.6589, 0.4254,
        0.5201, 0.5603, 0.3172, 0.7726, 0.5040, 0.5192, 0.4487, 0.4224, 0.4243,
        0.6657, 0.7103, 0.6792, 0.3307], device='cuda:0') tensor([0.5185, 0.5132, 0.4677, 0.5040, 0.4721, 0.4931, 0.5345, 0.5054, 0.4923,
        0.4727, 0.4813, 0.5004, 0.4830, 0.4808, 0.5365, 0.46

# Just 2 regressors to get xhat and yhat

In [205]:
class Model(nn.Module):
    def __init__(
        self
    ):
        super().__init__()
        
        
        self.predictory = nn.Sequential(
            nn.Linear(40, 64),
            nn.ReLU(),
            nn.Linear(64, 20),
            nn.Sigmoid()
        )
        
        self.predictorx = nn.Sequential(
            nn.Linear(20, 64),
            nn.ReLU(),
            nn.Linear(64, 40),
            nn.Sigmoid()
        )
        
            
    def forward(
        self,
        x,
    ):
        yhat = self.predictory(x)
        
        xhat = self.predictorx(yhat)
        
        
        return yhat, xhat

    
def reconstruction_loss(
    target,
    pred,
    batch_size
):
    
    recon_loss = F.l1_loss(pred, target, reduction='sum') / batch_size
    
    return recon_loss

def supervised_loss(
    target,
    pred,
    mu,
    logvar,
    batch_size
):
    # yhat_loss = F.l1_loss(pred, target, reduction='sum') / batch_size
    # yhat_loss = F.l1_loss(pred, target)

    # yhat_loss = torch.mean(0.5+0.5*(torch.div((muy-0.5).pow(2), logvary.exp()) + logvary))
    xl_mu = target.mean(dim=0)
    xl_std = target.std(dim=0)
    xl_std_tril = torch.diag_embed(xl_std)
    xl_sample = torch.distributions.MultivariateNormal(
        xl_mu,
        scale_tril=xl_std_tril
    ).sample(torch.Size([batch_size]))

    # print(target[0], yl_sample[0], yl_mu, yl_sample.mean(dim=0))
    
    xhat_mu = pred.mean(dim=0)
    xhat_std = pred.std(dim=0)
    xhat_std_tril = torch.diag_embed(xhat_std)
    xhat_sample = torch.distributions.MultivariateNormal(
        xhat_mu,
        scale_tril=xhat_std_tril
    ).sample(torch.Size([batch_size]))
    
    xhat_sample_loss = F.l1_loss(xhat_sample, xl_sample, reduction='sum') / batch_size
    xhat_loss = F.l1_loss(pred, target, reduction='sum') / batch_size
    # yhat_loss = F.kl_div(yhat_sample, yl_sample)
    xhat_prob_loss = torch.sum(torch.log(xhat_std) - torch.log(xl_std) + 0.5 * ( xl_std.pow(2) + ( xl_mu - xhat_mu )**2 ) / xhat_std.pow(2) - 0.5)
    
    # print(xhat_prob_loss, xhat_sample_loss, xhat_loss)

    # yhat_loss = yhat_sample_loss
    
    kl_loss = -0.5 * torch.sum(1 + logvar - mu.pow(2) - torch.exp(logvar))
    return xhat_loss + kl_loss, xhat_loss, kl_loss
    # return yhat_loss + kl_loss, yhat_loss, kl_loss

In [200]:
def test(
    model,
    dataset,
    L,
    epoch_num
):

        loss_x_epoch = 0
        r2_epoch = 0

        loss_recon_epoch = 0
        with torch.no_grad():
            for nbatch, (X,y) in enumerate(dataset):
                # so it is shape of [32, 1]
                # y = y[:, 0:1]
                
                
                y = y.to(device)
                y_deep = torch.clone(y)

                X = X.to(device)
                
                yhat, xhat = model(X)

                loss_x = F.l1_loss(X, xhat, reduction='sum') / X.shape[0]
                loss_recon = F.l1_loss(y, yhat, reduction='sum') / X.shape[0]
                
                loss_x_epoch += loss_x.item()
                loss_recon_epoch += loss_recon.item()
                
                r2 = r2_score(y, yhat, multioutput="raw_values")
                r2_mean = r2.mean()
                r2_epoch += r2_mean.item()

            print(
                "Test on y: ",
                yhat[0],
                y[0]
            )
            print(
                "Test on x: ",
                xhat[0],
                X[0]
            )
            
            loss_x_epoch = loss_x_epoch / len(dataset)
            loss_recon_epoch = loss_recon_epoch / len(dataset) 
            r2_epoch = r2_epoch / len(dataset)
            
            print(r2_epoch)

            return loss_x_epoch, loss_recon_epoch, r2_epoch
            



In [203]:
def train(
    model,
    dataset,
    L,
    u,
    r,
    noise_level,
    optimizer,
    epoch_num,
):
        loss_epoch  = 0

        recon_epoch_loss = 0
        
        supervised_epoch_loss = 0
        kl_epoch_loss = 0
    
        xl_epoch_loss = 0
        yresid_epoch_loss = 0
        yu_epoch_loss = 0


        for nbatch, (X,y) in enumerate(dataset):
            # so it is shape of [32, 1]
            # y = y[:, 0:1]
            
            y = y.to(device)
            # left only cell 7-6
            
            
            y_deep = torch.clone(y)

            Xl = X[:lbatch]
            Xu = X[lbatch:]
            # print(Xl.shape, Xu.shape)
            yl = y[:lbatch]
            yu = y[lbatch:]

            Xaug_up = torch.tensor([])
            Xaug_um = torch.tensor([])
            Xaug_lp = torch.tensor([])
            Xaug_lm = torch.tensor([])
            
            # Zero the gradients
            optimizer.zero_grad()
            
            Xl = Xl.to(device)
            Xu = Xu.to(device)
            
            Xaug_lp = Xaug_lp.to(device)
            Xaug_lm = Xaug_lm.to(device)
            
            Xaug_up = Xaug_up.to(device)
            Xaug_um = Xaug_um.to(device)
            


            if u != 0:
            
                labels_l, labels_um, labels_up = model(Xl, Xaug_um, Xaug_up)
                
                labels_upm = (labels_up + labels_um) / 2
    
                labels_upm_chunks = torch.reshape(
                    labels_upm, 
                    (L, int(labels_upm.shape[0]/L), labels_upm.shape[-1])
                )
                labels_upm = labels_upm_chunks.mean(dim=0)
                
                # lets say it is mean for u data
                labels_u = model(Xu, None, None)
                
                loss_u = unsupervised_loss(
                    labels_u,
                    labels_upm,
                    labels_u.shape[0]
                )
                yu_epoch_loss += loss_u.item()
    
                #supervised
                loss_l = supervised_loss(
                    yl,
                    labels_l,
                    Xl.shape[0]
                )
                
                yl_epoch_loss += loss_l.item()
    
                
                # # l + u only
                loss = loss_l + u*loss_u

            else:
                yhat, xhat = model(Xl)
                # yprior is true
                # x_decoded, yhat, mu, logvar, z = model(Xl, yl)
                # recon_yloss = reconstruction_loss(
                #     yl,
                #     yhat,
                #     yl.shape[0]
                # )
                # recon_yloss = torch.tensor(0)
                # recon_epoch_loss += recon_yloss.item()
                
                recon_xloss = reconstruction_loss(
                    Xl,
                    xhat,
                    yl.shape[0]
                )
                recon_epoch_loss += recon_xloss.item()
                

                # loss = r*recon_loss + s_loss + yhat_loss
                loss = r*recon_xloss # + recon_yloss
                
            
            loss.backward()
            optimizer.step()
            
            loss_epoch += loss.item()
            
    
        loss_epoch = loss_epoch / len(dataset)
        recon_epoch_loss = recon_epoch_loss / len(dataset)
        xl_epoch_loss = xl_epoch_loss / len(dataset)
        supervised_epoch_loss = supervised_epoch_loss / len(dataset)
        kl_epoch_loss = kl_epoch_loss / len(dataset)
    
        print(
            supervised_epoch_loss,
            recon_epoch_loss
        )

        return loss_epoch, recon_epoch_loss, xl_epoch_loss, kl_epoch_loss


        



In [204]:
# U = [0.01, 0.1, 1]
# U = [3, 5]
U = [0]
# Ls = [1,2,3,4,5,6,7,8,9,10]
# Ls = [1, 8, 16]
Ls = [1]
# R = [0.01, 1, 10]
R = [1]

noise=0.1

for u in U:
    for L in Ls:
        for r in R:
            # writer = SummaryWriter(f'svae/2splits_cv_1label_L_{train_size}_bs_{lbatch}/extend_z_shape_recon_coef_{r}_yprior')
            # writer = SummaryWriter(f'svae/2splits_cv_1label_L_{train_size}_bs_{lbatch}/ykldiv_bsnorm_recon_coef_{r}')
            writer = SummaryWriter(f'svae/2splits_cv_1label_L_{train_size}_bs_{lbatch}_reverse_task_y_isunknown/bsnorm_recon_coef_{r}_xu_norm_Xextended_2regressors_noyisgiven')
            
            train_loss_cv, train_xl_loss_cv, train_recon_loss_cv, train_kl_loss_cv = [], [], [], []
            test_loss_cv, test_recon_cv, test_r2_cv = [], [], []
            
            # for (xy_train, xy_test) in cv_datasets:
            # instead of cv we do run same model multiple times to average results
            xy_train, xy_test = cv_datasets[0]
            for _ in range(1):
                model = Model().to(device)
                adam = torch.optim.Adam(model.parameters())
                epoch = 1000
    
                train_loss_epoches, train_xl_loss_epoches, train_recon_loss_epoches, train_kl_loss_epoches = [], [], [], []
                test_loss_epoches, test_recon_epoches, test_r2_epoches = [], [], []
                for e in range(epoch):
                    train_loss_epoch, train_recon_epoch_loss, train_xl_epoch_loss, train_kl_epoch_loss = train(
                        model,
                        xy_train,
                        L,
                        u,
                        r,
                        noise,
                        adam,
                        e
                    )
                    train_loss_epoches.append(train_loss_epoch)
                    train_xl_loss_epoches.append(train_xl_epoch_loss)
                    
                    train_recon_loss_epoches.append(train_recon_epoch_loss)
                    
                    train_kl_loss_epoches.append(train_kl_epoch_loss)
                     
                    test_loss_epoch, test_recon_epoch, test_r2_epoch = test(
                        model,
                        xy_test,
                        L,
                        e
                    )
                    test_loss_epoches.append(test_loss_epoch)
                    test_r2_epoches.append(test_r2_epoch)
                    test_recon_epoches.append(test_recon_epoch)
                
                train_loss_cv.append(train_loss_epoches.copy())
                train_xl_loss_cv.append(train_xl_loss_epoches.copy())
    
                train_recon_loss_cv.append(train_recon_loss_epoches.copy())
                
                train_kl_loss_cv.append(train_kl_loss_epoches.copy())
                
                test_loss_cv.append(test_loss_epoches.copy())
                test_recon_cv.append(test_recon_epoches.copy())
                test_r2_cv.append(test_r2_epoches.copy())
            
            # averaging results over cv
            train_loss_cv = np.asarray(train_loss_cv).mean(axis=0)
            train_xl_loss_cv = np.asarray(train_xl_loss_cv).mean(axis=0)
    
            train_recon_loss_cv =np.asarray(train_recon_loss_cv).mean(axis=0)
            train_kl_loss_cv = np.asarray(train_kl_loss_cv).mean(axis=0)
            
            test_loss_cv = np.asarray(test_loss_cv).mean(axis=0)
            test_recon_cv = np.asarray(test_recon_cv).mean(axis=0)
            test_r2_cv = np.asarray(test_r2_cv).mean(axis=0)
            
            # adding to writer
            for e in range(len(test_loss_cv)):
                # print(e)
                writer.add_scalar('Train/epoch_loss', train_loss_cv[e], global_step=e)
                writer.add_scalar('Train/xl_Loss', train_xl_loss_cv[e], global_step=e)
                writer.add_scalar('Train/kl_Loss', train_kl_loss_cv[e], global_step=e)
                writer.add_scalar('Train/recon_Loss', train_recon_loss_cv[e], global_step=e)
                            
                
                writer.add_scalar('Test/x_loss', test_loss_cv[e], global_step=e)
                writer.add_scalar('Test/recon_loss', test_recon_cv[e], global_step=e)
                writer.add_scalar('Test/r2_mean', test_r2_cv[e], global_step=e)
            # if u == 0:
            #     break

0.0 4.218435972929001
Test on y:  tensor([0.4981, 0.5090, 0.3748, 0.4404, 0.4377, 0.5469, 0.5289, 0.4991, 0.3988,
        0.5074, 0.5198, 0.5427, 0.3746, 0.4644, 0.4189, 0.5236, 0.4952, 0.5113,
        0.5330, 0.5163], device='cuda:0') tensor([0.5057, 0.9288, 0.8095, 0.6554, 0.7195, 0.6465, 0.6041, 0.6612, 0.5192,
        0.6500, 0.5486, 0.5359, 0.5359, 0.4845, 0.6459, 0.5532, 0.2151, 0.5193,
        0.1823, 0.2330], device='cuda:0')
Test on x:  tensor([0.5042, 0.4827, 0.4995, 0.4810, 0.5062, 0.5233, 0.4840, 0.4882, 0.4648,
        0.4906, 0.4604, 0.4800, 0.4564, 0.4993, 0.4838, 0.4290, 0.5245, 0.4878,
        0.5378, 0.4934, 0.4940, 0.4947, 0.4951, 0.5320, 0.4949, 0.5121, 0.5008,
        0.5159, 0.5033, 0.5316, 0.5106, 0.5285, 0.5173, 0.4830, 0.4889, 0.5123,
        0.4852, 0.4743, 0.5003, 0.4998], device='cuda:0') tensor([0.6221, 0.1881, 0.2652, 0.5133, 0.3888, 0.4913, 0.5677, 0.5157, 0.5589,
        0.4381, 0.4283, 0.4844, 0.3880, 0.4807, 0.3942, 0.4563, 0.7544, 0.4327,
        0.68

In [ ]:
  # # aug supervised
            # # chunks to average res
            # labels_augl_chunks = torch.reshape(
            #     labels_augl, 
            #     (L, int(labels_augl.shape[0]/L), labels_augl.shape[-1])
            
            # )
            # labels_augl_mean = labels_augl_chunks.mean(dim=0)
            # # calc upon true yl
            # loss_augl_true = unsupervised_loss(
            #     yl,
            #     labels_augl_chunks,
            #     yl.shape[0]
            # )
            # yaugl_true_loss = loss_augl_true.item()

            # # calc upon aug mean
            # loss_augl = unsupervised_loss(
            #     labels_augl_mean,
            #     labels_augl_chunks,
            #     labels_augl_mean.shape[0]
            # )
            # yaugl_loss = loss_augl.item()

            # # perfect case when it's around 0
            # loss_yaugl = torch.abs(
            #     (torch.abs(loss_augl_true) - torch.abs(loss_augl))
            # )

In [34]:
# yaug = 0.1

def get_noise(loc, scale, size, coef=0.1):
    
    tril = torch.diag_embed(scale)
    mvn = torch.distributions.MultivariateNormal(
        loc,
        scale_tril=tril
    )
    samples = mvn.sample(torch.Size([size]))
    res = ( samples - samples.mean(dim=0) )*coef

    return res

def get_row_noise(batch, coef):
    # columns_shape = batch.shape[-1]
    columns_mean = batch.mean(dim=1)

    noise1 = torch.rand(*batch.shape)*coef
    noise2 = torch.rand(*batch.shape)*coef

    noise = noise1 - noise2
    # print(batch[0], noise[0] + batch[0])
    # print(batch[0].mean(), (noise[0] + batch[0]).mean())
    return noise
    
    

def train(
    model,
    dataset,
    L,
    u,
    noise_level,
    optimizer,
    epoch_num,
):
        loss_epoch  = 0
        
        yl_epoch_loss = 0
        yresid_epoch_loss = 0
        yu_epoch_loss = 0


        for nbatch, (X,y) in enumerate(dataset):
            # so it is shape of [32, 1]
            y = y[:, 0:1]
            
            y = y.to(device)
            # left only cell 7-6
            
            
            y_deep = torch.clone(y)

            Xl = X[:lbatch]
            Xu = X[lbatch:]
            # print(Xl.shape, Xu.shape)
            yl = y[:lbatch]
            yu = y[lbatch:]

            Xaug_up = torch.tensor([])
            Xaug_um = torch.tensor([])
            Xaug_lp = torch.tensor([])
            Xaug_lm = torch.tensor([])
            
            for _ in range(L):
                # aug l part
                
                noise_l = get_row_noise(Xl, noise_level)
                
                Xaug_lp = torch.cat(
                    (
                        Xaug_lp,
                        Xl + noise_l    
                    ),
                    dim=0
                )
                Xaug_lm = torch.cat(
                    (
                        Xaug_lm,
                        Xl - noise_l    
                    ),
                    dim=0
                )
                # print(nbatch, Xl[0])
                
                # aug u part
                noise_u = get_row_noise(Xu, noise_level)
                
                # add
                Xaug_up = torch.cat(
                    (
                        Xaug_up,
                        Xu + noise_u    
                    ),
                    dim=0
                )
                # print(Xu[0], noise_u[0], Xaug_up[0])
                # sub
                Xaug_um = torch.cat(
                    (
                        Xaug_um,
                        Xu - noise_u    
                    ),
                    dim=0
                )
            
            # Zero the gradients
            optimizer.zero_grad()
            
            Xl = Xl.to(device)
            Xu = Xu.to(device)
            
            Xaug_lp = Xaug_lp.to(device)
            Xaug_lm = Xaug_lm.to(device)
            
            Xaug_up = Xaug_up.to(device)
            Xaug_um = Xaug_um.to(device)
            

            

            if u != 0:
            
                # labels_lp = model(Xaug_lp)
                # labels_lm = model(Xaug_lm)
                # labels_lpm = (labels_lp + labels_lm) / 2
    
                # labels_lpm_chunks = torch.reshape(
                #     labels_lpm, 
                #     (L, int(labels_lpm.shape[0]/L), labels_lpm.shape[-1])
                # )
                # labels_lpm = labels_lpm_chunks.mean(dim=0)
    
                labels_l, labels_um, labels_up = model(Xl, Xaug_um, Xaug_up)
                
                labels_upm = (labels_up + labels_um) / 2
    
                labels_upm_chunks = torch.reshape(
                    labels_upm, 
                    (L, int(labels_upm.shape[0]/L), labels_upm.shape[-1])
                )
                labels_upm = labels_upm_chunks.mean(dim=0)
                
                # lets say it is mean for u data
                labels_u = model(Xu, None, None)
                
                loss_u = unsupervised_loss(
                    labels_u,
                    labels_upm,
                    labels_u.shape[0]
                )
                yu_epoch_loss += loss_u.item()
    
                #supervised
                loss_l = supervised_loss(
                    yl,
                    labels_l,
                    Xl.shape[0]
                )
                
                yl_epoch_loss += loss_l.item()
    
                # yl_ylpm_resid = torch.abs(labels_lpm - labels_l).sum() / Xl.shape[0]
                # # just to store
                # yresid_epoch_loss += yl_ylpm_resid.item()
                # l + residuals l and lpm + u 
                # loss = loss_l + yl_ylpm_resid - u*loss_u
                
                # # l + u only
                loss = loss_l + u*loss_u

            else:
                labels_l = model(Xl, None, None)
                loss_l = supervised_loss(
                    yl,
                    labels_l,
                    Xl.shape[0]
                )
                yl_epoch_loss += loss_l.item()
                loss = loss_l
            
            loss.backward()
            optimizer.step()
            
            loss_epoch += loss.item()
            
        
        
    
        loss_epoch = loss_epoch / len(dataset)
        yl_epoch_loss = yl_epoch_loss / len(dataset)
        yresid_epoch_loss = yresid_epoch_loss / len(dataset)
        yu_epoch_loss = yu_epoch_loss / len(dataset)
    
        print(
            yu_epoch_loss,
            yl_epoch_loss,
            
        )

        return loss_epoch, yl_epoch_loss, yresid_epoch_loss, yu_epoch_loss


        

